In [1]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [2]:
%run ../moreprocessing.py

In [3]:
# Find relevant information from annotations in soft file
df = pd.DataFrame(pd.read_csv('GPL13607_old_annotations.txt', sep = '\t', header=0, skiprows=11))
df

ID        ProbeName     GB_ACC  ControlType  \
0          1  GE_BrightCorner        NaN            1   
1          2       DarkCorner        NaN            1   
2          3       DarkCorner        NaN            1   
3          4     A_23_P326296  NM_144987            0   
4          5     A_24_P287941  NM_013290            0   
...      ...              ...        ...          ...   
62971  62972     A_23_P100386  NM_152456            0   
62972  62973       DarkCorner        NaN            1   
62973  62974       DarkCorner        NaN            1   
62974  62975  GE_BrightCorner        NaN            1   
62975  62976  GE_BrightCorner        NaN            1   

                                              accessions         GeneName  \
0                                                    NaN  GE_BrightCorner   
1                                                    NaN       DarkCorner   
2                                                    NaN       DarkCorner   
3      ref|NM_144987|ref|NM_001040425|ens|ENST0000029...          U2AF1L4   
4      ref|NM_013290|ref|NM_016556|ens|ENST0000039379...          PSMC3IP   
...                                                  ...              ...   
62971  ref|NM_152456|ens|ENST00000429149|ens|ENST0000...             IL34   
62972                                                NaN       DarkCorner   
62973                                                NaN       DarkCorner   
62974                                                NaN  GE_BrightCorner   
62975                                                NaN  GE_BrightCorner   

                                             Description  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3      ref|Homo sapiens U2 small nuclear RNA auxiliar...   
4      ref|Homo sapiens PSMC3 interacting protein (PS...   
...                                                  ...   
62971  ref|Homo sapiens interleukin 34 (IL34), mRNA [...   
62972                                                NaN   
62973                                                NaN   
62974                                                NaN   
62975                                                NaN   

                          chr_coord  \
0                               NaN   
1                               NaN   
2                               NaN   
3      hs|chr19:036235296-036235237   
4      hs|chr17:040724775-040724716   
...                             ...   
62971                      unmapped   
62972                           NaN   
62973                           NaN   
62974                           NaN   
62975                           NaN   

                                                SEQUENCE            SPOT_ID  
0                                                    NaN  --GE_BrightCorner  
1                                                    NaN       --DarkCorner  
2                                                    NaN       --DarkCorner  
3      GTATGGGGAGATTGAAGAGATGAATGTGTGCGACAACCTTGGGGAC...                NaN  
4      AAATTGCAGTAGCTTGAGGTTAACATTTAGACTTGGAACAATGCTA...                NaN  
...                                                  ...                ...  
62971  ACTTCAGTACATGAAACACTACTTCCCCATCAACTACAAGATCAGT...                NaN  
62972                                                NaN       --DarkCorner  
62973                                                NaN       --DarkCorner  
62974                                                NaN  --GE_BrightCorner  
62975                                                NaN  --GE_BrightCorner  

[62976 rows x 10 columns]

In [4]:
# Read expr file made using process.py
expr = pd.DataFrame(pd.read_csv('GSE65239-GPL13607-expr.txt', sep = '\t', header=0))
expr

ProbeID                                               Name  GSM1590586  \
0            1                                   GE_BrightCorner:   -0.453180   
1            2                                        DarkCorner:   -0.100115   
2            3                                        DarkCorner:   -0.030969   
3            4  U2AF1L4:ref|Homo sapiens U2 small nuclear RNA ...    0.400066   
4            5  PSMC3IP:ref|Homo sapiens PSMC3 interacting pro...    0.087819   
...        ...                                                ...         ...   
62971    62972  IL34:ref|Homo sapiens interleukin 34 (IL34), m...    0.483493   
62972    62973                                        DarkCorner:    0.123063   
62973    62974                                        DarkCorner:   -0.009545   
62974    62975                                   GE_BrightCorner:   -0.440949   
62975    62976                                   GE_BrightCorner:   -0.440711   

       GSM1590587  GSM1590588  GSM1590589  GSM1590590  GSM1590591  GSM1590592  \
0       -0.437613   -0.478821   -0.402059   -0.272282   -0.266545   -0.437065   
1       -0.010219    0.078874    0.089446    0.027102   -0.049688   -0.018174   
2       -0.051386    0.192394   -0.028843    0.009029    0.024290   -0.024022   
3        0.299219    0.180094    0.307975    0.129154    0.294646    0.242883   
4        0.186684    0.159291    0.140556    0.128769    0.139619    0.100405   
...           ...         ...         ...         ...         ...         ...   
62971    0.446707    0.444344    0.551002    0.545689    0.309582    0.544232   
62972    0.051887    0.030912    0.099044   -0.020640   -0.074185    0.019135   
62973    0.030383   -0.022276    0.016390   -0.027909   -0.018405   -0.030224   
62974   -0.456355   -0.445582   -0.353340   -0.265430   -0.274755   -0.387480   
62975   -0.413696   -0.440091   -0.342635   -0.265879   -0.268187   -0.379499   

       GSM1590593  GSM1590594  GSM1590595  GSM1590596  GSM1590597  GSM1590598  \
0       -0.309058   -0.258979   -0.377413   -0.321401   -0.292073   -0.374295   
1       -0.024723    0.043831    0.060698   -0.003665   -0.005351    0.179957   
2       -0.014977   -0.033858    0.022909    0.128274    0.016959    0.034080   
3        0.471886    0.220265    0.203533    0.242994    0.224390    0.354210   
4        0.098076    0.031956    0.058391    0.015888    0.063065    0.094859   
...           ...         ...         ...         ...         ...         ...   
62971    0.379855    0.442475    0.513696    0.464285    0.491916    0.550689   
62972   -0.060258    0.003777   -0.012965    0.028029    0.003354   -0.018804   
62973   -0.053734   -0.011281   -0.005963    0.117540    0.025881    0.013077   
62974   -0.329763   -0.284042   -0.380833   -0.316783   -0.264314   -0.352690   
62975   -0.321843   -0.256633   -0.374981   -0.305262   -0.264659   -0.412607   

       GSM1590599  GSM1590600  GSM1590601  GSM1590602  
0       -0.330242   -0.351269   -0.380806   -0.410159  
1        0.042752   -0.013954    0.143907   -0.021103  
2       -0.003517   -0.018968    0.112321    0.003860  
3        0.359002    0.188020    0.152267    0.229680  
4       -0.079609    0.171108    0.173655    0.003016  
...           ...         ...         ...         ...  
62971    0.400858    0.555873    0.504415    0.437649  
62972    0.026329   -0.040687   -0.047491    0.059484  
62973   -0.044967    0.041558    0.007361   -0.028290  
62974   -0.332713   -0.324257   -0.339333   -0.435771  
62975   -0.337557   -0.323210   -0.328869   -0.426770  

[62976 rows x 19 columns]

In [5]:
# Fix expr file
expr["ProbeID"] = df["ProbeName"]
expr["Name"] = df["GeneName"]
expr

ProbeID             Name  GSM1590586  GSM1590587  GSM1590588  \
0      GE_BrightCorner  GE_BrightCorner   -0.453180   -0.437613   -0.478821   
1           DarkCorner       DarkCorner   -0.100115   -0.010219    0.078874   
2           DarkCorner       DarkCorner   -0.030969   -0.051386    0.192394   
3         A_23_P326296          U2AF1L4    0.400066    0.299219    0.180094   
4         A_24_P287941          PSMC3IP    0.087819    0.186684    0.159291   
...                ...              ...         ...         ...         ...   
62971     A_23_P100386             IL34    0.483493    0.446707    0.444344   
62972       DarkCorner       DarkCorner    0.123063    0.051887    0.030912   
62973       DarkCorner       DarkCorner   -0.009545    0.030383   -0.022276   
62974  GE_BrightCorner  GE_BrightCorner   -0.440949   -0.456355   -0.445582   
62975  GE_BrightCorner  GE_BrightCorner   -0.440711   -0.413696   -0.440091   

       GSM1590589  GSM1590590  GSM1590591  GSM1590592  GSM1590593  GSM1590594  \
0       -0.402059   -0.272282   -0.266545   -0.437065   -0.309058   -0.258979   
1        0.089446    0.027102   -0.049688   -0.018174   -0.024723    0.043831   
2       -0.028843    0.009029    0.024290   -0.024022   -0.014977   -0.033858   
3        0.307975    0.129154    0.294646    0.242883    0.471886    0.220265   
4        0.140556    0.128769    0.139619    0.100405    0.098076    0.031956   
...           ...         ...         ...         ...         ...         ...   
62971    0.551002    0.545689    0.309582    0.544232    0.379855    0.442475   
62972    0.099044   -0.020640   -0.074185    0.019135   -0.060258    0.003777   
62973    0.016390   -0.027909   -0.018405   -0.030224   -0.053734   -0.011281   
62974   -0.353340   -0.265430   -0.274755   -0.387480   -0.329763   -0.284042   
62975   -0.342635   -0.265879   -0.268187   -0.379499   -0.321843   -0.256633   

       GSM1590595  GSM1590596  GSM1590597  GSM1590598  GSM1590599  GSM1590600  \
0       -0.377413   -0.321401   -0.292073   -0.374295   -0.330242   -0.351269   
1        0.060698   -0.003665   -0.005351    0.179957    0.042752   -0.013954   
2        0.022909    0.128274    0.016959    0.034080   -0.003517   -0.018968   
3        0.203533    0.242994    0.224390    0.354210    0.359002    0.188020   
4        0.058391    0.015888    0.063065    0.094859   -0.079609    0.171108   
...           ...         ...         ...         ...         ...         ...   
62971    0.513696    0.464285    0.491916    0.550689    0.400858    0.555873   
62972   -0.012965    0.028029    0.003354   -0.018804    0.026329   -0.040687   
62973   -0.005963    0.117540    0.025881    0.013077   -0.044967    0.041558   
62974   -0.380833   -0.316783   -0.264314   -0.352690   -0.332713   -0.324257   
62975   -0.374981   -0.305262   -0.264659   -0.412607   -0.337557   -0.323210   

       GSM1590601  GSM1590602  
0       -0.380806   -0.410159  
1        0.143907   -0.021103  
2        0.112321    0.003860  
3        0.152267    0.229680  
4        0.173655    0.003016  
...           ...         ...  
62971    0.504415    0.437649  
62972   -0.047491    0.059484  
62973    0.007361   -0.028290  
62974   -0.339333   -0.435771  
62975   -0.328869   -0.426770  

[62976 rows x 19 columns]

In [6]:
writeExprIdx(expr)

22-Jun-2022 11:20:02 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE65239 already exists. Skipping.
22-Jun-2022 11:20:02 INFO GEOparse - File already exist: using local version.
22-Jun-2022 11:20:02 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE65239/GSE65239_family.soft.gz: 
22-Jun-2022 11:20:03 DEBUG GEOparse - DATABASE: GeoMiame
22-Jun-2022 11:20:03 DEBUG GEOparse - SERIES: GSE65239
22-Jun-2022 11:20:03 DEBUG GEOparse - PLATFORM: GPL13607
22-Jun-2022 11:20:03 DEBUG GEOparse - SAMPLE: GSM1590586
22-Jun-2022 11:20:03 DEBUG GEOparse - SAMPLE: GSM1590587
22-Jun-2022 11:20:03 DEBUG GEOparse - SAMPLE: GSM1590588
22-Jun-2022 11:20:03 DEBUG GEOparse - SAMPLE: GSM1590589
22-Jun-2022 11:20:03 DEBUG GEOparse - SAMPLE: GSM1590590
22-Jun-2022 11:20:04 DEBUG GEOparse - SAMPLE: GSM1590591
22-Jun-2022 11:20:04 DEBUG GEOparse - SAMPLE: GSM1590592
22-Jun-2022 11:20:04 DEBUG GEOparse - SAMPLE: GSM1590593
22-Jun-2022 11:20:04 DEBUG GE

Starting expr
Done writing expr
Starting make_idx
Done with make_idx


In [ ]:
path_dir = "./"
expr.to_csv(path_dir+"GSE128027-GPL16791-expr.txt", header=True, index=False,sep='\t')
expr